In [1]:
DEBUG = True

In [2]:
import csv
import pandas as pd

genome_tags = pd.read_csv('src/data/genome-tags.csv')
if DEBUG:
    print(genome_tags)

      tagId           tag
0         1           007
1         2  007 (series)
2         3  18th century
3         4         1920s
4         5         1930s
...     ...           ...
1123   1124       writing
1124   1125         wuxia
1125   1126          wwii
1126   1127        zombie
1127   1128       zombies

[1128 rows x 2 columns]


In [3]:
Genres = ['Action', 'Adventure', 'Animation', 'Children',
          'Comedy', 'Crime', 'Documentary', 'Drama', 'Fantasy',
          'Film-Noir', 'Horror', 'IMAX', 'Musical', 'Mystery', 'Romance',
          'Sci-Fi', 'Thriller', 'War', 'Western', '(no genres listed)']

In [4]:
movies = pd.read_csv('src/data/movies.csv')
if DEBUG:
    print(movies)

       movieId                               title  \
0            1                    Toy Story (1995)   
1            2                      Jumanji (1995)   
2            3             Grumpier Old Men (1995)   
3            4            Waiting to Exhale (1995)   
4            5  Father of the Bride Part II (1995)   
...        ...                                 ...   
62418   209157                           We (2018)   
62419   209159           Window of the Soul (2001)   
62420   209163                    Bad Poems (2018)   
62421   209169                 A Girl Thing (2001)   
62422   209171      Women of Devil's Island (1962)   

                                            genres  
0      Adventure|Animation|Children|Comedy|Fantasy  
1                       Adventure|Children|Fantasy  
2                                   Comedy|Romance  
3                             Comedy|Drama|Romance  
4                                           Comedy  
...                              

In [5]:
genome_scores = pd.read_csv('src/data/genome-scores.csv')
if DEBUG:
    print(genome_scores)

          movieId  tagId  relevance
0               1      1    0.02875
1               1      2    0.02375
2               1      3    0.06250
3               1      4    0.07575
4               1      5    0.14075
...           ...    ...        ...
15584443   206499   1124    0.11000
15584444   206499   1125    0.04850
15584445   206499   1126    0.01325
15584446   206499   1127    0.14025
15584447   206499   1128    0.03350

[15584448 rows x 3 columns]


In [6]:
ratings = pd.read_csv('src/data/ratings.csv')
if DEBUG:
    print(ratings)

          userId  movieId  rating   timestamp
0              1      296     5.0  1147880044
1              1      306     3.5  1147868817
2              1      307     5.0  1147868828
3              1      665     5.0  1147878820
4              1      899     3.5  1147868510
...          ...      ...     ...         ...
25000090  162541    50872     4.5  1240953372
25000091  162541    55768     2.5  1240951998
25000092  162541    56176     2.0  1240950697
25000093  162541    58559     4.0  1240953434
25000094  162541    63876     5.0  1240952515

[25000095 rows x 4 columns]


In [7]:
ratings = ratings.sort_values(by=['timestamp'])
if DEBUG:
    print(ratings)

          userId  movieId  rating   timestamp
326761      2262       21     3.0   789652009
326810      2262     1079     3.0   789652009
326767      2262       47     5.0   789652009
15845015  102689        1     4.0   822873600
15845023  102689       39     5.0   822873600
...          ...      ...     ...         ...
13207880   85523   168252     4.0  1574327479
1284508     8642   202101     2.0  1574327512
13207893   85523   204704     4.0  1574327533
1284464     8642   122914     4.0  1574327549
13207877   85523   149406     4.5  1574327703

[25000095 rows x 4 columns]


In [8]:
tags = pd.read_csv('src/data/tags.csv')
if DEBUG:
    print(tags)

         userId  movieId                  tag   timestamp
0             3      260              classic  1439472355
1             3      260               sci-fi  1439472256
2             4     1732          dark comedy  1573943598
3             4     1732       great dialogue  1573943604
4             4     7569     so bad it's good  1573943455
...         ...      ...                  ...         ...
1093355  162521    66934  Neil Patrick Harris  1427311611
1093356  162521   103341     cornetto trilogy  1427311259
1093357  162534   189169               comedy  1527518175
1093358  162534   189169             disabled  1527518181
1093359  162534   189169              robbery  1527518193

[1093360 rows x 4 columns]


In [9]:
moviesIds = list(set(ratings.set_index('movieId').index.values))
moviesIds.sort()

In [10]:
movie_genres = movies.drop(columns=['movieId', 'title'])
movie_genres_dict = {'movieIds': [], 'genres': []}
for i in moviesIds:
    genres = movie_genres.loc[movies['movieId'] == i]
    movie_genres_dict['movieIds'].append(i)
    movie_genres_dict['genres'].append(genres['genres'].values[0].split('|'))
    if DEBUG:
        if i % 10000 == 0:
            print(i)
            
movies_genres_pd = pd.DataFrame(movie_genres_dict, columns=['movieIds', 'genres'])

if DEBUG:
    print(movies_genres_pd)

130000
140000
150000
160000
170000
200000
       movieIds                                             genres
0             1  [Adventure, Animation, Children, Comedy, Fantasy]
1             2                     [Adventure, Children, Fantasy]
2             3                                  [Comedy, Romance]
3             4                           [Comedy, Drama, Romance]
4             5                                           [Comedy]
...         ...                                                ...
59042    209157                                            [Drama]
59043    209159                                      [Documentary]
59044    209163                                    [Comedy, Drama]
59045    209169                               [(no genres listed)]
59046    209171                         [Action, Adventure, Drama]

[59047 rows x 2 columns]


In [10]:
ratings_temp = ratings.drop(columns=['timestamp', 'userId']).set_index('movieId')
ratings_temp = ratings_temp.join(movies.set_index('movieId')).drop(columns=['title'])

ratings_for_genres = {'Genre name' : [], 'Mean rating' : []}

for i in Genres:
    x = ratings_temp.loc[ratings_temp['genres'].str.contains(i)].drop(columns=['genres'])
    if DEBUG:
        print(i)
        print(x.mean().values[0])
    ratings_for_genres['Genre name'].append(i)
    ratings_for_genres['Mean rating'].append(x.mean().values[0])

Action
3.4665917497681593
Adventure
3.517444633654892
Animation
3.614946348438093
Comedy
3.4239925478057365
Crime
3.685043693003225
Documentary
3.7052805249822454
Drama
3.677184674800756
Fantasy
3.5115889157486
Film-Noir
3.9257281769386028
Horror
3.2935633075659174
Musical
3.554715987107105
Mystery
3.670169244577933
Romance
3.5427121571630567
Sci-Fi
3.4781433928067798
Thriller
3.5229643285084498
War
3.7914657875591984
Western
3.5857553061515595


/home/nhemisirmkow/Studia/Erasmus/Zajęcia/SocialVenv/lib/python3.7/site-packages/pandas/core/strings.py:1952: UserWarning: This pattern has match groups. To actually get the groups, use str.extract.
  return func(self, *args, **kwargs)


(no genres listed)
3.326379239118188


In [11]:
ratings_for_genres = pd.DataFrame.from_dict(ratings_for_genres).set_index("Genre name")
ratings_for_genres.to_csv("output/genres_mean_ratings.csv")

if DEBUG:
    print(ratings_for_genres)

                    Mean rating
Genre name                     
Action                 3.466592
Adventure              3.517445
Animation              3.614946
Comedy                 3.423993
Crime                  3.685044
Documentary            3.705281
Drama                  3.677185
Fantasy                3.511589
Film-Noir              3.925728
Horror                 3.293563
Musical                3.554716
Mystery                3.670169
Romance                3.542712
Sci-Fi                 3.478143
Thriller               3.522964
War                    3.791466
Western                3.585755
(no genres listed)     3.326379


In [12]:
new_ratings = ratings.loc[ratings['timestamp'] >= 1420070400]
ratings = new_ratings
print(ratings)

          userId  movieId  rating   timestamp
13321588   86188     1196     3.5  1420070535
13321586   86188     1036     4.0  1420070551
13321645   86188    58559     3.0  1420070568
13321578   86188      110     2.5  1420070579
13321580   86188      293     3.5  1420070583
...          ...      ...     ...         ...
13207880   85523   168252     4.0  1574327479
1284508     8642   202101     2.0  1574327512
13207893   85523   204704     4.0  1574327533
1284464     8642   122914     4.0  1574327549
13207877   85523   149406     4.5  1574327703

[7563741 rows x 4 columns]


In [13]:
ratings_temp = ratings.drop(columns=['userId']).sort_values(by=['movieId', 'timestamp'])
if DEBUG:
    print(ratings_temp)
    
ratings_temp = ratings_temp.set_index('movieId')

for i in range(11):
    temp = ratings_temp.loc[i * 20000 : (i + 1) * 20000, :]
    print(temp)
    temp.to_csv("output/ratings_sorted" + str(i * 20000) + "-" + str((i + 1) * 20000) + "__.csv")
    


          movieId  rating   timestamp
5119148         1     5.0  1420087507
447035          1     3.5  1420097365
13841732        1     4.5  1420102669
9428426         1     2.0  1420112716
5739334         1     3.0  1420148490
...           ...     ...         ...
18457961   209157     1.5  1574280748
17864443   209159     3.0  1574280985
1036618    209163     4.5  1574284913
18457962   209169     3.0  1574291826
18457963   209171     3.0  1574291937

[7563741 rows x 3 columns]
         rating   timestamp
movieId                    
1           5.0  1420087507
1           3.5  1420097365
1           4.5  1420102669
1           2.0  1420112716
1           3.0  1420148490
...         ...         ...
9018        3.5  1546835784
9018        2.0  1553134754
9018        3.5  1563511212
9018        2.0  1570228245
9019        5.0  1501258202

[3574782 rows x 2 columns]
         rating   timestamp
movieId                    
25735       3.0  1439912698
25735       3.0  1447225294
25735       

In [23]:
temp = pd.read_csv("output/chiTest1-20000.csv")

In [24]:
temp = temp.set_index('V1')

In [25]:
print(temp)

      Unnamed: 0            V2        V3        V4        V5
V1                                                          
1              1  0.000000e+00  0.279658  0.958427  0.114175
2              2  0.000000e+00  0.043238  0.146372  0.369765
3              3  0.000000e+00  0.473677  0.166721  0.725281
4              4  4.440892e-16  0.393468  0.705756  0.034033
5              5  0.000000e+00  0.749075  0.065717  0.495593
...          ...           ...       ...       ...       ...
9008        6996  8.425314e-01  0.043047  1.000000  0.005416
9010        6997  1.035878e-01  0.696057  0.794530  0.744772
9011        6998  1.857493e-01  0.467038  0.009919  0.354300
9013        6999  4.786762e-01  0.948649  0.176227  1.000000
9018        7000  5.475706e-04  0.483343  0.453691  0.961587

[7000 rows x 5 columns]


In [47]:
temp = temp.join(movies_genres_pd.set_index('movieIds'))
temp = temp.drop(columns=['Unnamed: 0'])

In [48]:
print(temp)

                V2        V3        V4        V5  \
V1                                                 
1     0.000000e+00  0.279658  0.958427  0.114175   
2     0.000000e+00  0.043238  0.146372  0.369765   
3     0.000000e+00  0.473677  0.166721  0.725281   
4     4.440892e-16  0.393468  0.705756  0.034033   
5     0.000000e+00  0.749075  0.065717  0.495593   
...            ...       ...       ...       ...   
9008  8.425314e-01  0.043047  1.000000  0.005416   
9010  1.035878e-01  0.696057  0.794530  0.744772   
9011  1.857493e-01  0.467038  0.009919  0.354300   
9013  4.786762e-01  0.948649  0.176227  1.000000   
9018  5.475706e-04  0.483343  0.453691  0.961587   

                                                 genres  
V1                                                       
1     [Adventure, Animation, Children, Comedy, Fantasy]  
2                        [Adventure, Children, Fantasy]  
3                                     [Comedy, Romance]  
4                              [C

In [58]:
all_gen = { i : 0 for i in Genres }
print(all_gen)
good_gen = { i : 0 for i in Genres }
print(good_gen)

{'Action': 0, 'Adventure': 0, 'Animation': 0, 'Children': 0, 'Comedy': 0, 'Crime': 0, 'Documentary': 0, 'Drama': 0, 'Fantasy': 0, 'Film-Noir': 0, 'Horror': 0, 'IMAX': 0, 'Musical': 0, 'Mystery': 0, 'Romance': 0, 'Sci-Fi': 0, 'Thriller': 0, 'War': 0, 'Western': 0, '(no genres listed)': 0}
{'Action': 0, 'Adventure': 0, 'Animation': 0, 'Children': 0, 'Comedy': 0, 'Crime': 0, 'Documentary': 0, 'Drama': 0, 'Fantasy': 0, 'Film-Noir': 0, 'Horror': 0, 'IMAX': 0, 'Musical': 0, 'Mystery': 0, 'Romance': 0, 'Sci-Fi': 0, 'Thriller': 0, 'War': 0, 'Western': 0, '(no genres listed)': 0}


In [59]:
for index, row in temp.iterrows():
#     print(row)
    for i in row['genres']:
        if (row['V2'] < 0.05):
            good_gen[i] = good_gen[i] + 1
        all_gen[i] = all_gen[i] + 1

In [60]:
print(all_gen)
print(good_gen)

{'Action': 1021, 'Adventure': 722, 'Animation': 191, 'Children': 418, 'Comedy': 2545, 'Crime': 802, 'Documentary': 240, 'Drama': 3346, 'Fantasy': 372, 'Film-Noir': 88, 'Horror': 707, 'IMAX': 22, 'Musical': 286, 'Mystery': 379, 'Romance': 1212, 'Sci-Fi': 550, 'Thriller': 1193, 'War': 297, 'Western': 178, '(no genres listed)': 0}
{'Action': 522, 'Adventure': 379, 'Animation': 113, 'Children': 224, 'Comedy': 1077, 'Crime': 333, 'Documentary': 61, 'Drama': 1306, 'Fantasy': 195, 'Film-Noir': 42, 'Horror': 288, 'IMAX': 11, 'Musical': 108, 'Mystery': 187, 'Romance': 522, 'Sci-Fi': 270, 'Thriller': 586, 'War': 135, 'Western': 63, '(no genres listed)': 0}


In [66]:
current = 1
for index, row in ratings.iterrows():
    print(row['rating'])
    current = current + 1
    if ((row['rating'] * 2) % 2 == 1):
        print(row, current)
        break

3.0
3.0
5.0
4.0
5.0
4.0
5.0
5.0
4.0
5.0
4.0
5.0
5.0
4.0
3.0
5.0
1.0
5.0
5.0
5.0
5.0
3.0
4.0
4.0
3.0
5.0
4.0
3.0
4.0
1.0
4.0
3.0
4.0
5.0
4.0
4.0
4.0
5.0
4.0
4.0
5.0
5.0
4.0
5.0
5.0
5.0
5.0
5.0
4.0
5.0
3.0
1.0
4.0
5.0
2.0
5.0
1.0
4.0
3.0
2.0
5.0
3.0
3.0
1.0
4.0
4.0
3.0
3.0
3.0
3.0
4.0
4.0
1.0
3.0
4.0
2.0
3.0
3.0
4.0
4.0
4.0
2.0
4.0
4.0
3.0
2.0
3.0
1.0
5.0
4.0
2.0
3.0
3.0
3.0
3.0
4.0
3.0
3.0
5.0
4.0
1.0
4.0
4.0
3.0
4.0
4.0
3.0
4.0
5.0
5.0
5.0
5.0
5.0
4.0
3.0
4.0
3.0
3.0
3.0
5.0
2.0
1.0
4.0
3.0
2.0
1.0
5.0
5.0
4.0
3.0
4.0
3.0
2.0
2.0
3.0
4.0
1.0
5.0
4.0
4.0
3.0
5.0
1.0
5.0
4.0
5.0
5.0
5.0
4.0
5.0
1.0
5.0
5.0
5.0
4.0
1.0
4.0
4.0
3.0
2.0
3.0
1.0
4.0
3.0
3.0
3.0
4.0
5.0
2.0
2.0
2.0
5.0
5.0
4.0
3.0
2.0
4.0
1.0
5.0
3.0
4.0
3.0
5.0
5.0
5.0
3.0
5.0
4.0
3.0
5.0
4.0
3.0
5.0
4.0
5.0
1.0
4.0
3.0
4.0
4.0
3.0
4.0
3.0
5.0
5.0
4.0
5.0
4.0
3.0
4.0
3.0
3.0
5.0
4.0
4.0
2.0
5.0
4.0
4.0
3.0
5.0
1.0
3.0
5.0
3.0
4.0
5.0
3.0
4.0
4.0
3.0
3.0
4.0
3.0
3.0
5.0
5.0
3.0
4.0
5.0
4.0
1.0
5.0
5.0
3.0
5.0
5.0
4.0
5.0
2.0


5.0
5.0
5.0
5.0
3.0
5.0
5.0
4.0
1.0
5.0
2.0
2.0
5.0
2.0
5.0
3.0
4.0
4.0
4.0
5.0
3.0
5.0
4.0
5.0
5.0
4.0
4.0
5.0
5.0
5.0
4.0
5.0
5.0
4.0
5.0
4.0
4.0
5.0
3.0
1.0
2.0
3.0
2.0
3.0
3.0
2.0
1.0
5.0
4.0
3.0
4.0
5.0
1.0
2.0
5.0
2.0
2.0
5.0
4.0
3.0
5.0
5.0
5.0
5.0
4.0
5.0
5.0
4.0
4.0
4.0
5.0
4.0
4.0
4.0
5.0
5.0
5.0
4.0
2.0
4.0
5.0
5.0
4.0
5.0
4.0
3.0
5.0
5.0
5.0
4.0
3.0
5.0
4.0
5.0
3.0
4.0
4.0
5.0
4.0
1.0
5.0
1.0
5.0
4.0
4.0
2.0
2.0
4.0
5.0
5.0
4.0
5.0
4.0
3.0
5.0
3.0
3.0
3.0
2.0
5.0
5.0
5.0
5.0
4.0
4.0
3.0
5.0
3.0
4.0
5.0
5.0
5.0
4.0
4.0
5.0
4.0
5.0
5.0
5.0
5.0
3.0
5.0
2.0
5.0
5.0
5.0
3.0
5.0
1.0
5.0
5.0
4.0
3.0
4.0
5.0
4.0
5.0
2.0
3.0
3.0
4.0
4.0
4.0
5.0
4.0
5.0
4.0
5.0
5.0
3.0
5.0
5.0
5.0
3.0
2.0
5.0
4.0
5.0
5.0
2.0
3.0
4.0
5.0
1.0
5.0
3.0
5.0
4.0
4.0
4.0
4.0
4.0
4.0
5.0
4.0
4.0
4.0
4.0
5.0
2.0
4.0
4.0
5.0
3.0
4.0
5.0
5.0
2.0
5.0
5.0
5.0
4.0
4.0
3.0
5.0
4.0
5.0
3.0
5.0
4.0
5.0
5.0
4.0
4.0
4.0
5.0
4.0
5.0
3.0
4.0
5.0
5.0
4.0
5.0
5.0
5.0
5.0
5.0
5.0
5.0
4.0
3.0
3.0
2.0
4.0
4.0
5.0
4.0
5.0
5.0


5.0
5.0
3.0
2.0
3.0
5.0
4.0
5.0
4.0
4.0
5.0
5.0
5.0
5.0
3.0
4.0
4.0
4.0
5.0
5.0
4.0
5.0
5.0
4.0
5.0
3.0
4.0
5.0
4.0
5.0
2.0
4.0
5.0
3.0
4.0
3.0
5.0
4.0
4.0
3.0
1.0
5.0
4.0
2.0
3.0
3.0
3.0
2.0
5.0
3.0
4.0
3.0
4.0
3.0
5.0
3.0
3.0
5.0
4.0
5.0
4.0
4.0
3.0
3.0
5.0
3.0
3.0
3.0
5.0
1.0
3.0
3.0
3.0
3.0
3.0
4.0
3.0
3.0
4.0
4.0
3.0
2.0
3.0
4.0
3.0
5.0
5.0
5.0
3.0
4.0
4.0
4.0
5.0
5.0
3.0
4.0
4.0
5.0
4.0
5.0
1.0
2.0
4.0
5.0
5.0
5.0
4.0
5.0
4.0
5.0
3.0
5.0
5.0
3.0
3.0
5.0
4.0
4.0
4.0
5.0
1.0
3.0
3.0
5.0
3.0
4.0
5.0
5.0
4.0
4.0
3.0
3.0
3.0
2.0
4.0
5.0
5.0
4.0
4.0
5.0
5.0
5.0
4.0
4.0
4.0
4.0
4.0
4.0
3.0
5.0
4.0
4.0
5.0
4.0
3.0
3.0
1.0
1.0
4.0
3.0
5.0
1.0
4.0
3.0
4.0
3.0
5.0
4.0
4.0
5.0
5.0
5.0
5.0
4.0
5.0
5.0
4.0
4.0
3.0
3.0
3.0
3.0
5.0
1.0
4.0
2.0
4.0
5.0
5.0
5.0
5.0
5.0
4.0
4.0
4.0
5.0
5.0
3.0
4.0
5.0
5.0
4.0
2.0
5.0
4.0
4.0
4.0
5.0
4.0
4.0
5.0
3.0
2.0
5.0
5.0
3.0
5.0
5.0
5.0
5.0
5.0
5.0
4.0
5.0
5.0
5.0
5.0
5.0
4.0
5.0
5.0
5.0
5.0
5.0
5.0
5.0
5.0
5.0
3.0
5.0
4.0
4.0
4.0
5.0
3.0
5.0
5.0
5.0
5.0
4.0


4.0
2.0
5.0
5.0
4.0
3.0
5.0
5.0
4.0
5.0
5.0
5.0
4.0
5.0
2.0
4.0
4.0
3.0
4.0
5.0
4.0
3.0
4.0
4.0
4.0
5.0
5.0
2.0
5.0
5.0
5.0
5.0
4.0
5.0
5.0
3.0
4.0
4.0
5.0
5.0
5.0
4.0
3.0
5.0
5.0
5.0
4.0
4.0
5.0
4.0
4.0
5.0
5.0
5.0
4.0
5.0
5.0
2.0
4.0
4.0
4.0
4.0
5.0
5.0
5.0
4.0
5.0
4.0
5.0
4.0
5.0
5.0
4.0
3.0
4.0
2.0
2.0
4.0
3.0
3.0
2.0
4.0
4.0
3.0
4.0
5.0
4.0
4.0
4.0
5.0
5.0
5.0
4.0
4.0
4.0
4.0
4.0
4.0
5.0
3.0
4.0
4.0
4.0
4.0
4.0
5.0
4.0
4.0
4.0
4.0
3.0
4.0
4.0
4.0
5.0
5.0
5.0
5.0
5.0
3.0
5.0
3.0
5.0
5.0
4.0
4.0
5.0
5.0
5.0
4.0
5.0
5.0
5.0
3.0
3.0
3.0
2.0
3.0
4.0
2.0
3.0
4.0
3.0
5.0
1.0
3.0
5.0
3.0
5.0
4.0
3.0
2.0
5.0
4.0
5.0
5.0
5.0
5.0
5.0
3.0
3.0
3.0
5.0
4.0
5.0
3.0
5.0
5.0
5.0
4.0
5.0
2.0
3.0
4.0
3.0
5.0
5.0
4.0
1.0
4.0
4.0
5.0
5.0
4.0
3.0
5.0
4.0
5.0
4.0
4.0
5.0
5.0
5.0
4.0
5.0
4.0
5.0
4.0
5.0
4.0
5.0
5.0
5.0
5.0
5.0
4.0
5.0
5.0
5.0
4.0
5.0
4.0
5.0
5.0
4.0
4.0
5.0
3.0
5.0
4.0
3.0
4.0
4.0
2.0
5.0
2.0
5.0
2.0
5.0
3.0
3.0
5.0
4.0
3.0
3.0
2.0
4.0
5.0
3.0
5.0
5.0
4.0
5.0
4.0
5.0
5.0
1.0
4.0
3.0
4.0


1.0
4.0
5.0
4.0
5.0
1.0
5.0
4.0
4.0
5.0
3.0
4.0
4.0
3.0
2.0
5.0
4.0
4.0
5.0
5.0
4.0
3.0
5.0
3.0
5.0
4.0
4.0
3.0
5.0
5.0
4.0
3.0
4.0
4.0
5.0
5.0
4.0
3.0
1.0
4.0
5.0
4.0
3.0
4.0
5.0
2.0
5.0
4.0
5.0
4.0
5.0
4.0
3.0
4.0
4.0
5.0
2.0
4.0
5.0
4.0
4.0
5.0
5.0
4.0
4.0
4.0
4.0
5.0
5.0
4.0
5.0
5.0
4.0
5.0
4.0
5.0
4.0
4.0
3.0
3.0
4.0
4.0
5.0
5.0
5.0
5.0
3.0
4.0
5.0
5.0
4.0
3.0
4.0
4.0
5.0
3.0
4.0
4.0
4.0
5.0
5.0
3.0
4.0
4.0
5.0
4.0
4.0
5.0
5.0
5.0
5.0
5.0
4.0
5.0
2.0
4.0
4.0
5.0
5.0
4.0
3.0
1.0
3.0
4.0
3.0
4.0
5.0
5.0
4.0
4.0
4.0
5.0
3.0
3.0
4.0
4.0
1.0
5.0
5.0
1.0
4.0
4.0
3.0
4.0
5.0
5.0
4.0
4.0
4.0
4.0
5.0
5.0
4.0
4.0
5.0
4.0
4.0
5.0
3.0
4.0
4.0
5.0
4.0
3.0
5.0
4.0
5.0
5.0
4.0
5.0
5.0
4.0
4.0
5.0
4.0
4.0
3.0
3.0
4.0
4.0
1.0
5.0
4.0
4.0
4.0
5.0
4.0
5.0
4.0
5.0
4.0
4.0
5.0
4.0
5.0
3.0
4.0
2.0
4.0
4.0
2.0
3.0
4.0
4.0
5.0
3.0
4.0
5.0
5.0
3.0
5.0
4.0
4.0
3.0
4.0
4.0
3.0
4.0
1.0
3.0
4.0
4.0
3.0
4.0
4.0
5.0
5.0
5.0
3.0
5.0
5.0
4.0
3.0
5.0
1.0
5.0
3.0
4.0
1.0
1.0
3.0
4.0
5.0
4.0
5.0
3.0
4.0
4.0
4.0
3.0


...

4.0
4.0
3.0
3.0
5.0
5.0
3.0
4.0
3.0
4.0
3.0
4.0
1.0
2.0
3.0
4.0
5.0
4.0
3.0
3.0
3.0
3.0
3.0
4.0
3.0
3.0
4.0
3.0
3.0
4.0
1.0
3.0
5.0
3.0
3.0
3.0
5.0
3.0
4.0
3.0
4.0
3.0
3.0
4.0
2.0
3.0
1.0
5.0
4.0
4.0
4.0
5.0
4.0
3.0
4.0
4.0
3.0
3.0
3.0
3.0
5.0
2.0
4.0
4.0
5.0
2.0
4.0
4.0
3.0
3.0
3.0
3.0
5.0
3.0
5.0
3.0
3.0
5.0
5.0
3.0
3.0
4.0
4.0
3.0
3.0
1.0
5.0
4.0
3.0
3.0
4.0
4.0
5.0
2.0
1.0
5.0
3.0
4.0
2.0
2.0
3.0
5.0
3.0
4.0
3.0
3.0
4.0
3.0
3.0
3.0
5.0
3.0
3.0
4.0
3.0
5.0
3.0
3.0
3.0
4.0
3.0
5.0
3.0
2.0
4.0
3.0
5.0
5.0
3.0
3.0
2.0
4.0
4.0
3.0
2.0
2.0
4.0
2.0
3.0
5.0
5.0
3.0
4.0
4.0
5.0
2.0
3.0
3.0
5.0
3.0
3.0
3.0
1.0
5.0
3.0
3.0
3.0
3.0
3.0
2.0
4.0
2.0
3.0
1.0
2.0
2.0
3.0
3.0
3.0
5.0
3.0
1.0
3.0
1.0
5.0
3.0
3.0
1.0
1.0
3.0
4.0
2.0
5.0
2.0
4.0
5.0
3.0
2.0
5.0
3.0
3.0
3.0
5.0
4.0
4.0
3.0
4.0
4.0
3.0
5.0
5.0
3.0
3.0
2.0
3.0
5.0
4.0
3.0
3.0
5.0
3.0
5.0
3.0
3.0
4.0
4.0
3.0
3.0
4.0
5.0
2.0
3.0
4.0
3.0
4.0
3.0
5.0
4.0
4.0
2.0
3.0
3.0
3.0
2.0
3.0
5.0
4.0
3.0
2.0
3.0
3.0
4.0
3.0
3.0
1.0
3.0
3.0
3.0
4.0
3.0


3.0
4.0
4.0
2.0
3.0
5.0
5.0
3.0
3.0
4.0
3.0
3.0
4.0
4.0
3.0
3.0
4.0
3.0
4.0
4.0
4.0
3.0
3.0
3.0
3.0
4.0
3.0
3.0
3.0
4.0
4.0
3.0
3.0
3.0
4.0
3.0
3.0
3.0
3.0
3.0
4.0
4.0
4.0
3.0
5.0
4.0
3.0
4.0
3.0
3.0
3.0
3.0
3.0
4.0
3.0
5.0
3.0
3.0
3.0
3.0
3.0
3.0
3.0
3.0
3.0
3.0
2.0
4.0
3.0
4.0
5.0
4.0
3.0
4.0
4.0
4.0
3.0
4.0
3.0
4.0
3.0
5.0
4.0
4.0
5.0
3.0
3.0
1.0
3.0
5.0
3.0
3.0
3.0
4.0
4.0
3.0
3.0
3.0
1.0
5.0
3.0
4.0
4.0
5.0
4.0
5.0
2.0
4.0
1.0
4.0
5.0
4.0
5.0
3.0
5.0
4.0
4.0
3.0
5.0
3.0
1.0
4.0
4.0
4.0
4.0
5.0
4.0
3.0
4.0
3.0
4.0
5.0
4.0
4.0
3.0
4.0
3.0
3.0
5.0
5.0
3.0
4.0
4.0
5.0
4.0
5.0
4.0
3.0
3.0
3.0
5.0
5.0
3.0
3.0
3.0
3.0
3.0
3.0
4.0
4.0
3.0
3.0
4.0
3.0
5.0
5.0
3.0
5.0
3.0
3.0
4.0
2.0
5.0
3.0
3.0
3.0
4.0
4.0
3.0
3.0
4.0
4.0
4.0
4.0
3.0
3.0
4.0
4.0
5.0
5.0
3.0
3.0
5.0
4.0
3.0
3.0
4.0
3.0
5.0
3.0
5.0
5.0
4.0
3.0
4.0
4.0
5.0
3.0
3.0
4.0
3.0
4.0
2.0
3.0
3.0
5.0
5.0
3.0
4.0
3.0
3.0
4.0
3.0
3.0
4.0
4.0
3.0
5.0
4.0
5.0
5.0
4.0
3.0
5.0
4.0
3.0
3.0
5.0
5.0
4.0
2.0
4.0
3.0
3.0
3.0
3.0
4.0
5.0
4.0
5.0


5.0
3.0
3.0
5.0
4.0
4.0
4.0
5.0
4.0
4.0
5.0
4.0
4.0
4.0
3.0
5.0
3.0
4.0
5.0
4.0
3.0
5.0
5.0
2.0
5.0
2.0
5.0
4.0
4.0
3.0
4.0
4.0
5.0
4.0
4.0
5.0
4.0
4.0
4.0
5.0
4.0
5.0
4.0
4.0
3.0
4.0
5.0
4.0
5.0
4.0
4.0
4.0
3.0
4.0
3.0
4.0
4.0
5.0
4.0
3.0
4.0
3.0
2.0
4.0
3.0
2.0
3.0
4.0
4.0
3.0
4.0
3.0
3.0
4.0
5.0
5.0
5.0
3.0
5.0
2.0
4.0
5.0
4.0
5.0
5.0
5.0
5.0
5.0
4.0
5.0
4.0
3.0
3.0
3.0
3.0
3.0
3.0
3.0
3.0
3.0
4.0
3.0
2.0
3.0
4.0
3.0
5.0
5.0
4.0
4.0
3.0
3.0
5.0
3.0
3.0
4.0
5.0
4.0
2.0
4.0
4.0
3.0
3.0
3.0
4.0
2.0
3.0
3.0
3.0
4.0
3.0
3.0
5.0
4.0
4.0
3.0
4.0
3.0
3.0
5.0
5.0
4.0
3.0
5.0
5.0
4.0
3.0
5.0
1.0
5.0
5.0
1.0
3.0
4.0
5.0
4.0
4.0
4.0
3.0
3.0
3.0
4.0
4.0
3.0
4.0
4.0
4.0
4.0
3.0
3.0
4.0
3.0
3.0
3.0
5.0
4.0
3.0
3.0
3.0
3.0
2.0
3.0
3.0
3.0
4.0
3.0
3.0
3.0
2.0
3.0
4.0
3.0
5.0
3.0
3.0
1.0
3.0
4.0
4.0
3.0
4.0
3.0
3.0
3.0
3.0
3.0
4.0
5.0
3.0
4.0
3.0
3.0
3.0
5.0
4.0
4.0
2.0
5.0
3.0
4.0
3.0
3.0
3.0
3.0
3.0
4.0
2.0
1.0
3.0
4.0
2.0
1.0
1.0
3.0
3.0
1.0
2.0
4.0
3.0
3.0
5.0
5.0
3.0
3.0
4.0
2.0
3.0
3.0
4.0
4.0


4.0
5.0
4.0
3.0
5.0
5.0
3.0
4.0
5.0
5.0
4.0
5.0
3.0
3.0
5.0
4.0
5.0
5.0
4.0
5.0
5.0
4.0
4.0
3.0
4.0
3.0
5.0
5.0
3.0
4.0
4.0
4.0
5.0
5.0
5.0
4.0
3.0
5.0
4.0
5.0
4.0
3.0
2.0
4.0
5.0
4.0
4.0
3.0
3.0
5.0
4.0
4.0
2.0
5.0
4.0
5.0
3.0
5.0
4.0
5.0
4.0
2.0
3.0
4.0
5.0
4.0
3.0
4.0
4.0
2.0
4.0
3.0
4.0
5.0
3.0
4.0
2.0
5.0
3.0
3.0
3.0
3.0
4.0
3.0
4.0
3.0
3.0
5.0
1.0
5.0
1.0
3.0
4.0
3.0
2.0
3.0
4.0
4.0
2.0
2.0
5.0
3.0
3.0
2.0
3.0
4.0
4.0
4.0
4.0
1.0
3.0
4.0
4.0
4.0
3.0
3.0
2.0
3.0
3.0
1.0
3.0
5.0
3.0
3.0
3.0
4.0
4.0
1.0
3.0
5.0
4.0
3.0
4.0
3.0
3.0
3.0
5.0
2.0
4.0
3.0
5.0
4.0
5.0
3.0
4.0
3.0
3.0
2.0
1.0
3.0
4.0
3.0
3.0
5.0
3.0
5.0
5.0
3.0
4.0
3.0
5.0
1.0
1.0
2.0
5.0
1.0
3.0
3.0
3.0
3.0
1.0
4.0
1.0
2.0
3.0
4.0
4.0
3.0
4.0
3.0
5.0
4.0
4.0
5.0
3.0
5.0
4.0
3.0
3.0
3.0
4.0
2.0
3.0
3.0
5.0
3.0
3.0
4.0
3.0
3.0
4.0
4.0
2.0
3.0
4.0
5.0
3.0
4.0
3.0
4.0
4.0
4.0
4.0
3.0
5.0
5.0
5.0
3.0
3.0
4.0
3.0
3.0
3.0
5.0
5.0
4.0
3.0
5.0
5.0
5.0
3.0
4.0
4.0
3.0
3.0
3.0
4.0
4.0
3.0
3.0
4.0
4.0
4.0
3.0
4.0
5.0
5.0
4.0
5.0
5.0


KeyboardInterrupt: 

In [73]:
print(ratings.loc[(ratings['rating'] * 2) % 2 == 1])

          userId  movieId  rating   timestamp
24707235  160540     2918     4.5  1045604890
8015644    52178     1339     4.5  1045606417
8015726    52178     1997     4.5  1045606427
8015875    52178     3147     4.5  1045606429
8015523    52178      253     4.5  1045606434
...          ...      ...     ...         ...
13207874   85523   122916     4.5  1574327389
13207872   85523   122912     4.5  1574327399
13207855   85523    60069     4.5  1574327406
13207868   85523   109487     4.5  1574327445
13207877   85523   149406     4.5  1574327703

[7433212 rows x 4 columns]


In [74]:
print(ratings.loc[ratings['timestamp'] < 1045604890])

          userId  movieId  rating   timestamp
326761      2262       21     3.0   789652009
326810      2262     1079     3.0   789652009
326767      2262       47     5.0   789652009
15845015  102689        1     4.0   822873600
15845023  102689       39     5.0   822873600
...          ...      ...     ...         ...
17489000  113317     1036     3.0  1045604828
17488983  113317      165     3.0  1045604828
17489013  113317     1370     3.0  1045604828
17489014  113317     1584     3.0  1045604843
17489039  113317     4014     3.0  1045604863

[7111522 rows x 4 columns]
